In [1]:
from unidecode import unidecode
import os
import pandas as pd
import re
import requests
from bs4 import BeautifulSoup
import time
from selenium import webdriver #Webdriver de Selenium qui permet de contrôler un navigateur
from selenium.webdriver.common.by import By #Permet d'accéder aux différents élements de la page web
from webdriver_manager.chrome import ChromeDriverManager #Assure la gestion du webdriver de Chrome
from datetime import datetime, timedelta
import math
import time
import warnings
warnings.filterwarnings("ignore")
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import itertools
import os
import re
import chardet
from bs4 import BeautifulSoup
import xml.etree.ElementTree as ET
import pandas as pd
from bs4.element import NavigableString, Tag

In [2]:
def find_trs_files(folder_path):
    trs_paths = []
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            if file.endswith('.trs'):
                trs_paths.append(os.path.join(root, file))
    return trs_paths

In [3]:
def find_clapi_corpus(path):
    pattern = r'E:\\Corpus\\CLAPI_scrape\\Clapi_Transcription_([\S]+).trs'
    match = re.search(pattern, path)
    if match:
        corpus = match.group(1)
        return corpus
    else:
        return False

In [4]:
def detect_encoding(file):
    with open(file, 'rb') as f:
        result = chardet.detect(f.read())
        encoding = result['encoding'] 
    # Open the file with the detected encoding
    with open(file, 'r', encoding=encoding) as f:
        soup = BeautifulSoup(f, "lxml-xml")
    return soup

In [5]:
def get_all_tagsname(xml_file):
    try : 
        tree = ET.parse(xml_file)
    # Get the root element of the tree
        root = tree.getroot()
    # Initialize an empty set to store the tag names
        tag_names = set()
    # Iterate over all elements in the tree and add their tag names to the set
        for elem in root.iter():
            tag_names.add(elem.tag)
    # Return the set of tag names
    except: 
        return "Pas de fichier trouvé à cet emplacement"
    return tag_names

In [6]:
def parse_trs(path):
    soup = detect_encoding(path)
    tagsname = list(get_all_tagsname(path))
    if find_clapi_corpus(path):
        corpus = find_clapi_corpus(path)
        df = pd.DataFrame({'tagsname': [tagsname], 'corpus' : corpus, 'path_trs':path})
        return df
    else: 
        pass

In [7]:
def is_same(list1, list2):
    s = set(list2)
    difference = [x for x in list1 if x not in s]
    if difference : 
        return difference
    else: 
        return True

In [8]:
def get_difference(df):
    # prendre la liste des tags + l'intersection de toutes les listes
    lists_tags = df['tagsname'].tolist()
    results_union = set().union(*lists_tags)
    # trouver les différences entre l'intersection de toutes les listes et la liste des tags d'un corpus donné
    df['is_same'] = df['tagsname'].apply(lambda x:is_same(x, results_union))
    return results_union, df

In [9]:
def find_files_with_pattern(pattern, folder):
    # Create an empty list to store the matching files
    matching_files = []
    # Define the list of allowed file extensions
    allowed_extensions = ['.wav']#, '.mp3', '.mp4', '.avi', '.mkv', '.mov', '.flac']
    # Walk through all the files and directories in the folder and its subdirectories
    for root, dirs, files in os.walk(folder):
        # Iterate through all the files in the current directory
        for file in files:
            # Check if the file extension is allowed
            if os.path.splitext(file)[1] in allowed_extensions:
                # Check if the file name contains the pattern
                if pattern in file:
                    # If the pattern is found, add the file path to the list
                    matching_files.append(os.path.join(root, file))
    # Return the list of matching files
    return matching_files

In [10]:
def get_audio(file):
    soup = detect_encoding(file)
    audio_filename = soup.find('Trans')['audio_filename']
    return audio_filename.replace('_anon','').replace('-','_')

In [11]:
folder_path = 'E:\Corpus\CLAPI_scrape'
trs_paths = find_trs_files(folder_path)
liste_parsage = [parse_trs(trs) for trs in trs_paths]
df_corpus = pd.concat(liste_parsage, axis=0)

files_audio = []
for trs, corpus in list(zip(df_corpus['path_trs'].tolist(),df_corpus['corpus'].tolist())) :
    file = find_files_with_pattern(corpus, 'E:\Corpus\CLAPI_scrape')
    files_audio.append(file[0])
df_corpus['path_wav'] = files_audio

In [12]:
results_union_trs, df_corpus = get_difference(df_corpus)
print('Nb de tags communs :', len(results_union_trs), '\n Liste des tags communs :\n', results_union_trs)

Nb de tags communs : 13 
 Liste des tags communs :
 {'Section', 'Topics', 'Speaker', 'Turn', 'Topic', 'Background', 'Event', 'Trans', 'Who', 'Speakers', 'Comment', 'Episode', 'Sync'}


In [13]:
df_corpus = df_corpus.reset_index(drop=True)

In [14]:
df_corpus

tagsname  \
0   [Section, Sync, Turn, Event, Trans, Who, Speak...   
1   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
2   [Section, Sync, Turn, Event, Trans, Who, Speak...   
3   [Section, Sync, Turn, Event, Trans, Who, Speak...   
4   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
5   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
6   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
7               [Section, Turn, Trans, Episode, Sync]   
8   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
9   [Section, Sync, Turn, Event, Trans, Who, Speak...   
10  [Topics, Section, Sync, Topic, Turn, Event, Tr...   
11  [Section, Sync, Background, Turn, Event, Trans...   
12  [Section, Sync, Background, Turn, Event, Trans...   
13  [Topics, Section, Sync, Topic, Turn, Backgroun...   
14  [Section, Sync, Background, Turn, Event, Trans...   

                               corpus  \
0      aperitif_entre_ami(e)s_glasgow   
1         aperitif_entre_ami(e)s_pois   
2      aperitif_entre_ami(e)s_rupture   
3         aperitif_entre_ami(e)s_chat   
4          Boulangerie_rurale_C01_C20   
5                          Fromagerie   
6                      montage_meuble   
7          Boulangerie_rurale_C21_C41   
8   reunion_organisation_evenement_DH   
9      visites_guidees_manoir_Guide_1   
10     visites_guidees_manoir_Guide_2   
11                Bureau_CPE_probleme   
12                Bureau_CPE_Insultes   
13     visites_guidees_manoir_Guide_3   
14                 Bureau_CPE_bagarre   

                                             path_trs  \
0   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
1   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
2   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
3   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
4   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bou...   
5   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Fro...   
6   E:\Corpus\CLAPI_scrape\Clapi_Transcription_mon...   
7   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bou...   
8   E:\Corpus\CLAPI_scrape\Clapi_Transcription_reu...   
9   E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
10  E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
11  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   
12  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   
13  E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
14  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   

                                             path_wav  is_same  
0   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
1   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
2   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
3   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
4   E:\Corpus\CLAPI_scrape\Clapi_Signal_Boulangeri...     True  
5   E:\Corpus\CLAPI_scrape\Clapi_Signal_Fromagerie...     True  
6   E:\Corpus\CLAPI_scrape\Clapi_Signal_montage_me...     True  
7   E:\Corpus\CLAPI_scrape\Clapi_Signal_Boulangeri...     True  
8   E:\Corpus\CLAPI_scrape\Clapi_Signal_reunion_or...     True  
9   E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
10  E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
11  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True  
12  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True  
13  E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
14  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True

# prendre les métadonnées

In [15]:
def next_corpus(driver):
    corpus_suivant = driver.find_element(By.XPATH, "//input[@value='Corpus suivant']")
    corpus_suivant.click()
    return driver

In [16]:
def get_corpus_name(driver):
    page_source = driver.page_source
    soup = BeautifulSoup(page_source,features='html.parser')
    pattern = r'Corpus [0-9]+ sur 69 : (.*)' # Define the pattern using a regular expression
    tag = soup.find(text=re.compile(pattern)) # Find the tag that contains the pattern
    match = re.search(pattern, tag) # Extract the matching text using the regular expression pattern
    corpus_name = match.group(1) # Extract the text group and save it in the corpus_name variable
    return corpus_name # Print the corpus_name variable

In [17]:
def get_nb_enregistrement(driver):
    soup = BeautifulSoup(driver.page_source,features='html.parser')
    nb_enregistrements = int(soup.find('div', {'id':'u286_rtf'}).get_text().replace(' Enregistrements ', '').replace(' Enregistrement ', ''))
    return nb_enregistrements

In [18]:
def get_nom_enregistrement(driver):
    soup = BeautifulSoup(driver.page_source,features='html.parser')
    nom_enregistrement = soup.find('div', {'id':'u524_rtf'}).get_text().replace(' ', '').replace('-', '')
    return nom_enregistrement

In [19]:
def get_enregistrement_name(driver):
    nb_enregistrements = int(soup.find('div', {'id':'u286_rtf'}).get_text().replace(' Enregistrements ', '').replace(' Enregistrement ', ''))
    #liste_enregistrement = soup.find_all('div', {'id':'ou344'})
    liste_df = []
    for i in range(nb_enregistrements):
        liste_enregistrement = driver.find_elements(By.ID, "ou344")
        element = liste_enregistrement[i]
        soup = BeautifulSoup(driver.page_source,features='html.parser')
        nom_enregistrement = soup.find('div', {'id':'u524_rtf'}).get_text()
        if nom_enregistrement.replace('-', '').replace(' ', '').lower() == nom_enregistrement_file.replace('-', '').replace(' ', '').lower():
            True 
        else : 
            driver.execute_script("arguments[0].click();", element)
    return False

In [20]:
def get_element(liste):
    if not liste:
        liste = ''
    elif len(liste)>1:
        liste = liste[-1].get_text()
    elif len(liste) == 1:
        liste = liste[0].get_text()
    else : 
        liste = ''    
    return liste

In [21]:
def get_metadata_enregistrement(soup):
    nom_enregistrement = soup.find('div', {'id':'u524_rtf'}).get_text()
    description = soup.find_all('div', {'id':'u380'})
    description = get_element(description)

    data_collecte = soup.find_all('div', {'id':'u372_rtf'})
    data_collecte = get_element(data_collecte)

    duree = soup.find_all('div', {'id':'u374_rtf'})
    duree = get_element(duree)

    nb_locuteurs = soup.find_all('div', {'id':'u376_rtf'})
    nb_locuteurs = get_element(nb_locuteurs)
    langue_lieu = soup.find_all('div', {'id':'u378_rtf'})
    langue_lieu = get_element(langue_lieu)
    pat = r'([a-z-\u00C0-\u017F]+)([A-Z-\u00C0-\u017F]+.+)'
    match1 = re.search(pat, langue_lieu)
    if match1 : 
        langue_enregistrement = match1.group(1)
        lieu_enregistrement = match1.group(2)
    else:
        langue_enregistrement = langue_lieu
        lieu_enregistrement = langue_lieu
    table_locuteur = soup.find_all('div', {'id':'u392container'})
    
    if len(table_locuteur) > 0:
        table_locuteur = table_locuteur[-1]
        noms_locuteurs = [x.get_text() for x in table_locuteur.find_all('div', {'id':'u404_rtf'})]
        sexe_locuteurs = [x.get_text() for x in table_locuteur.find_all('div', {'id':'u406_rtf'})]
        age_locuteurs = [x.get_text() for x in table_locuteur.find_all('div', {'id':'u408_rtf'})]
        langue_locuteurs = [x.get_text() for x in table_locuteur.find_all('div', {'id':'u410_rtf'})]
        profession_locuteurs = [x.get_text() for x in table_locuteur.find_all('div', {'id':'u412_rtf'})]
        
        dict_loc = {}
        for index in range(len(noms_locuteurs)):
            pattern = r'([a-zA-Z]+([0-9]+|)) ([a-zA-Z]+([0-9]+|))'
            match = re.search(pattern, noms_locuteurs[index])
            if match :  
                dict_loc[index] = {
                'speaker': match.group(1),
                'nom':match.group(3),
                'sexe': sexe_locuteurs[index],
                'age': age_locuteurs[index],
                'profession': profession_locuteurs[index],
                'langue': langue_locuteurs[index]}
            else :  
                dict_loc[index] = {
                'speaker': noms_locuteurs[index],
                'nom':noms_locuteurs[index],
                'sexe': sexe_locuteurs[index],
                'age': age_locuteurs[index],
                'profession': profession_locuteurs[index],
                'langue': langue_locuteurs[index]}
    else:
        table_locuteur = "Non renseigné"
        noms_locuteurs = "Non renseigné"
        sexe_locuteurs = "Non renseigné"
        age_locuteurs = "Non renseigné"
        langue_locuteurs = "Non renseigné"
        profession_locuteurs = "Non renseigné"
        dict_loc = {}
    
    meta_enregistrement = {}
    meta_enregistrement['nom_enregistrement'] = nom_enregistrement
    meta_enregistrement['description_enregistrement'] = description
    meta_enregistrement['date_collecte_enregistrement'] = data_collecte
    meta_enregistrement['duree_enregistrement'] =  duree
    meta_enregistrement['nb_locuteurs_enregistrement'] = nb_locuteurs
    meta_enregistrement['langue_enregistrement']= langue_enregistrement
    meta_enregistrement['lieu_enregistrement']= lieu_enregistrement
    meta_enregistrement['locuteurs'] = dict_loc
    
    return meta_enregistrement

In [22]:
def get_metadata_corpus(soup):
    pattern = r'Corpus [0-9]+ sur 69 : (.*)' 
    tag = soup.find(text=re.compile(pattern))
    match = re.search(pattern, tag) 
    corpus_name = match.group(1) 
    metadata_corpus = soup.find('div', {'id':'u262container'})
    autrice_corpus = metadata_corpus.find('div', {'id':'u274_rtf'}).get_text()
    date_collecte_corpus = metadata_corpus.find('div', {'id':'u276_rtf'}).get_text()
    duree_corpus = metadata_corpus.find('div', {'id':'u280_rtf'}).get_text()
    langue_corpus = metadata_corpus.find('div', {'id':'u282_rtf'}).get_text()
    meta_corpus = {}
    meta_corpus['nom_corpus'] = corpus_name
    meta_corpus['responsable_corpus'] = autrice_corpus
    meta_corpus['duree_corpus'] = duree_corpus
    meta_corpus['langue_corpus'] = langue_corpus
    return meta_corpus

In [23]:
options = Options()
#options.headless = True

driver = webdriver.Chrome(ChromeDriverManager().install(),options=options)  #Initialisation du driver
driver.implicitly_wait(0.5)
time.sleep(3) #Ajout d'un temps de deux secondes avant de lancer l'action suivante
driver.get("http://clapi.icar.cnrs.fr/V3_Feuilleter.php?")

In [24]:
dict_meta = {}
for x in range(0,70): 
    nb_enregistrements = get_nb_enregistrement(driver)
    for i in range(nb_enregistrements):
        nom_enregistrement = unidecode(get_nom_enregistrement(driver).lower())
        if i == 0:
            try: 
                element = [elem for elem in driver.find_elements(By.ID, "ou344")][1]
            except:
                element = [elem for elem in driver.find_elements(By.ID, "ou344")][i]
        else: 
            element = [elem for elem in driver.find_elements(By.ID, "ou344")][i]
        if nom_enregistrement in [nom.replace(' ', '').replace('_','').lower() for nom in df_corpus['corpus'].tolist()]:
            print('oui', nom_enregistrement)
            soup = BeautifulSoup(driver.page_source,features='html.parser')
            corpus = get_metadata_corpus(soup)
            enregistrement = get_metadata_enregistrement(soup)
            dict_enre = {}
            dict_enre['corpus'] = corpus
            dict_enre['enregistrement']=enregistrement
            dict_meta['{}'.format(nom_enregistrement)]=dict_enre
            driver.execute_script("arguments[0].click();", element)
        else:
            print('__', nom_enregistrement)
            driver.execute_script("arguments[0].click();", element)
    next_corpus(driver)

oui aperitifentreami(e)schat
oui aperitifentreami(e)sglasgow
oui aperitifentreami(e)spois
oui aperitifentreami(e)srupture
__ coursdefiguration
__ coursdelinguistique
__ coursdelinguistique
__ latueriefinale
__ zwichenpinkundrot
__ inscriptional'universitelyon2
__ nosamislinguistes-coursd'expression
__ systemeuniversitairei
__ systemeuniversitaireii
__ chezleslogeurs
__ conversationatable
__ conversationatable
__ conversationsavecl'appareil
__ dansuncafe
__ deditepourlachambre
__ destoutespetiteslampesdanslaciel
__ iletaitpastoutnu
__ jeveuxfaireungateau
__ chezmmemouginpourtelephoner
__ chezuneamie
__ concert
__ handkasemitmusik
__ krautsalat
__ laconcierge
__ lamedecineparlesplantes
__ maisc'estlerhin!
__ qu'estcequec'estqu'unerandonnee?
__ retourdel'allemagne
__ soireelinguistes
__ soulc'estpasunmottresfrancais
__ undimancheapresmidi
__ unesoireecommune
__ visitechezl'anciennelogeuse
__ alaposte
__ aucreditagricole
__ aucreditagricole
__ chezledirecteurdufoyer
__ kaffeetrinken
__ lac

In [25]:
dict_meta #changer les locuteurs de sortent à extraire le nom du fichier ex JEA pour Jeanne

{'aperitifentreami(e)schat': {'corpus': {'nom_corpus': 'Apéritif entre ami(e)s - chat',
   'responsable_corpus': 'G. Icor, S. SchwarzConseil de gestion Clapi',
   'duree_corpus': '31m55s',
   'langue_corpus': 'Français'},
  'enregistrement': {'nom_enregistrement': 'Apéritif entre ami(e)s - chat',
   'description_enregistrement': 'Interaction entre quatre amis durant un apéritif.',
   'date_collecte_enregistrement': '21 Nov 2009',
   'duree_enregistrement': '31m55s',
   'nb_locuteurs_enregistrement': '4',
   'langue_enregistrement': 'français',
   'lieu_enregistrement': 'FRANCE  Région Lyonnaise',
   'locuteurs': {0: {'speaker': 'JUL',
     'nom': 'Julie',
     'sexe': 'Femme',
     'age': '20 - 30',
     'profession': 'en scolarité',
     'langue': ''},
    1: {'speaker': 'CLA',
     'nom': 'Claire',
     'sexe': 'Femme',
     'age': '20 - 30',
     'profession': '',
     'langue': 'français'},
    2: {'speaker': 'LAU',
     'nom': 'Laurent',
     'sexe': 'Homme',
     'age': '20 - 30'

In [26]:
df_corpus

tagsname  \
0   [Section, Sync, Turn, Event, Trans, Who, Speak...   
1   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
2   [Section, Sync, Turn, Event, Trans, Who, Speak...   
3   [Section, Sync, Turn, Event, Trans, Who, Speak...   
4   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
5   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
6   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
7               [Section, Turn, Trans, Episode, Sync]   
8   [Topics, Section, Sync, Topic, Turn, Event, Tr...   
9   [Section, Sync, Turn, Event, Trans, Who, Speak...   
10  [Topics, Section, Sync, Topic, Turn, Event, Tr...   
11  [Section, Sync, Background, Turn, Event, Trans...   
12  [Section, Sync, Background, Turn, Event, Trans...   
13  [Topics, Section, Sync, Topic, Turn, Backgroun...   
14  [Section, Sync, Background, Turn, Event, Trans...   

                               corpus  \
0      aperitif_entre_ami(e)s_glasgow   
1         aperitif_entre_ami(e)s_pois   
2      aperitif_entre_ami(e)s_rupture   
3         aperitif_entre_ami(e)s_chat   
4          Boulangerie_rurale_C01_C20   
5                          Fromagerie   
6                      montage_meuble   
7          Boulangerie_rurale_C21_C41   
8   reunion_organisation_evenement_DH   
9      visites_guidees_manoir_Guide_1   
10     visites_guidees_manoir_Guide_2   
11                Bureau_CPE_probleme   
12                Bureau_CPE_Insultes   
13     visites_guidees_manoir_Guide_3   
14                 Bureau_CPE_bagarre   

                                             path_trs  \
0   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
1   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
2   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
3   E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
4   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bou...   
5   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Fro...   
6   E:\Corpus\CLAPI_scrape\Clapi_Transcription_mon...   
7   E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bou...   
8   E:\Corpus\CLAPI_scrape\Clapi_Transcription_reu...   
9   E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
10  E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
11  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   
12  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   
13  E:\Corpus\CLAPI_scrape\Clapi_Transcription_vis...   
14  E:\Corpus\CLAPI_scrape\Clapi_Transcription_Bur...   

                                             path_wav  is_same  
0   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
1   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
2   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
3   E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...     True  
4   E:\Corpus\CLAPI_scrape\Clapi_Signal_Boulangeri...     True  
5   E:\Corpus\CLAPI_scrape\Clapi_Signal_Fromagerie...     True  
6   E:\Corpus\CLAPI_scrape\Clapi_Signal_montage_me...     True  
7   E:\Corpus\CLAPI_scrape\Clapi_Signal_Boulangeri...     True  
8   E:\Corpus\CLAPI_scrape\Clapi_Signal_reunion_or...     True  
9   E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
10  E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
11  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True  
12  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True  
13  E:\Corpus\CLAPI_scrape\Clapi_Signal_visites_gu...     True  
14  E:\Corpus\CLAPI_scrape\Clapi_Signal_Bureau_CPE...     True

In [27]:
def parse_trs2(file, corpus):
    print(file)
    soup, encoding = detect_encoding2(file)
    my_dict = {}
    dict_trans, audio_filename = get_trans2(soup, my_dict)
    my_dict.update(dict_trans)  
    my_dict.update(get_topics2(soup, my_dict))
    my_dict.update(get_section2(soup, my_dict))
    dict_turns = get_turn2(soup)
    df = pd.DataFrame.from_dict(dict_turns,orient='index')
    df['audio_filename']= audio_filename
    df['encoding']=encoding
    df['corpus']=corpus
    df = df.drop_duplicates().reset_index(drop=True)
    print('________________________________________')
    return df

In [28]:
def detect_encoding2(file):
    with open(file, 'rb') as f:
        result = chardet.detect(f.read())
        encoding = result['encoding'] 
    # Open the file with the detected encoding
    with open(file, 'r', encoding=encoding) as f:
        soup = BeautifulSoup(f, "lxml-xml")
    return soup, encoding

In [29]:
def flatten_list(liste):
    flattened_list = []
    for sublist in liste:
        for item in sublist:
            flattened_list.append(item)
    return flattened_list

In [30]:
def get_trans2(soup, my_dict):
    trans = soup.find('Trans')
    # create a dictionary of locuteurs
    if trans is not None:
        audio_filename = trans.get('audio_filename')
        my_dict['audio_filename'] = audio_filename
    return my_dict, audio_filename

def get_speaker2(soup):
    speakers = soup.find_all('Speaker')
    # create a dictionary of speakers
    my_dict = {}
    for speaker in speakers:
        scope = speaker.get('scope')
        accent = speaker.get('accent')
        dialect = speaker.get('dialect')
        check = speaker.get('check')
        name = speaker.get('name')
        id_ = speaker.get('id')
        # create a new dictionary for this speaker
        dict_locuteur = {}
        dict_locuteur['scope'] = scope
        dict_locuteur['accent'] = accent
        dict_locuteur['dialect'] = dialect
        dict_locuteur['check'] = check
        dict_locuteur['name'] = name
        dict_locuteur['id'] = id_
        my_dict[id_] = dict_locuteur
    return my_dict

def get_topics2(soup, my_dict):
    topics = soup.find_all('Topic')
    # create a dictionary of locuteurs
    for topic in topics:
        id_ = topic.get('id')
        desc = topic.get('desc')
        # create a new dictionary for this speaker
        dict_topic = {}
        dict_topic['desc'] = desc
        dict_topic['id'] = id_
        my_dict[id_] = dict_topic
    return my_dict

def get_section2(soup, my_dict):
    sections = soup.find_all('Section')
    # create a dictionary of locuteurs
    for section in sections:
        topic = section.get('topic')
        endTime = section.get('endTime')
        startTime = section.get('startTime')
        type_ = section.get('type')
        # create a new dictionary for this speaker
        dict_section = {}
        dict_section['topic'] = topic
        dict_section['startTime'] = startTime
        dict_section['endTime'] = endTime
        dict_section['type'] = type_
        my_dict['section_{}'.format(topic)] = dict_section
    return my_dict

def get_turn2(soup):
    turns = soup.find_all('Turn')
    dict_turns = {}
    dict_loc = get_speaker2(soup)
    results = []
    i = 0
    for index, turn in enumerate(turns):
        speaker = turn.get('speaker')
        if speaker is not None:
            speakers_ = r'([a-zA-Z]+([0-9]+|)) ([a-zA-Z]+([0-9]+|)) *([a-zA-Z]*([0-9]*|))'
            match = re.search(speakers_, speaker)
            if match :
                print('MULTI SPEAKER')
                print(turn)
                spk1 = match.group(1)
                spk2 = match.group(3)
                liste_speaker = [spk1, spk2]
                try:
                    spk3 = match.group(3)
                    liste_speaker.append(spk3)
                except:
                    pass
                result = get_sync_multiple_loc2(turn, liste_speaker)
                for spk,text in result:
                    print('spk:', spk, 'text: ', text)
                    endTime = turn.get('endTime')
                    startTime = turn.get('startTime')
                    dict_turn = {}
                    dict_turn['startTime']=startTime
                    print(type(startTime))
                    dict_turn['endTime']=endTime
                    dict_turn['speaker'] = dict_loc['{}'.format(spk)]['name']
                    dict_turn['speaker_native'] = dict_loc['{}'.format(spk)]['dialect']
                    dict_turn['text_synchronisé'] = str(((startTime, text.replace('\n',''))))
                    #dict_turn['speaker_characteristic'] = dict_loc.get('{}'.format(spk))
                    dict_turn['text']= text.replace('\n','')
                    dict_turns['{}'.format(i)] = dict_turn
                    print('_________________')
                    i+=1

                #prendre le texte de speaker 1 et le texte de speaker 2 AVEC **ALERT**
                # créer un tour par locuteur avec le même start et end time
            else: 
                print('UN SEUL SPEAKER')
                print(turn)
                endTime = turn.get('endTime')
                startTime = turn.get('startTime')
                sync_tags = turn.find_all('Sync')
                result = get_sync_times2(turn)
                text = turn.text.encode('iso-8859-1').decode('iso-8859-1')
                dict_turn = {}
                dict_turn['startTime']=startTime
                dict_turn['endTime']=endTime
                dict_turn['speaker'] = dict_loc['{}'.format(speaker)]['name']
                dict_turn['speaker_native'] = dict_loc['{}'.format(speaker)]['dialect']
                #dict_turn['speaker_characteristic'] = dict_loc.get('{}'.format(speaker))
                dict_turn['text']= text.replace('\n','')
                dict_turn['text_synchronisé'] = str(result).strip('[]')
                dict_turns['{}'.format(i)] = dict_turn
                print('spk: ', speaker, 'text : ', text.replace('\n',''))
                print('___________________')
                i+=1
        else:
            endTime = turn.get('endTime')
            startTime = turn.get('startTime')
            dict_turn = {}
            dict_turn['startTime']=startTime
            dict_turn['endTime']=endTime
            dict_turn['speaker']= turn.text.replace('\n','')+'***NO SPEAKER***'
            dict_turns['{}'.format(i)] = dict_turn
            print('No spk', 'action : ',turn.text.replace('\n','')+'***ACTIONS***' )
            print('---')
            i+=1
    return dict_turns

In [31]:
def get_sync_times2(turn):
    sync_tags = turn.find_all('Sync')
    list_sync = []
    for i, sync_tag in enumerate(sync_tags):  
        contenu = []
        # Récupérer le contenu jusqu'à la balise Sync suivante
        current_tag = sync_tag.next_sibling
        while current_tag is not None and current_tag.name != 'Sync':
            if isinstance(current_tag, NavigableString):
                current_tag_str = current_tag.get_text().replace('\n','').encode('iso-8859-1').decode('iso-8859-1')
                print(current_tag_str)
                contenu.append(current_tag_str)
            else:
                pass
            current_tag = current_tag.next_sibling
        #print(''.join(flatten_list(contenu)).get_text())
        list_sync.append((sync_tag['time'], contenu))
    return list_sync

In [32]:
def get_sync_multiple_loc(spk1, spk2, turn, spk3='spk3'):
    who_tags = turn.find_all('Who')
    list_ = []
    for index, who_tag in enumerate(who_tags):
        contenu = []
        # Récupérer le contenu jusqu'à la balise Sync suivante
        current_tag = who_tag.next_sibling
        print(index)
        print(who_tag)
        while current_tag is not None and current_tag.name != 'Who':
            if isinstance(current_tag, NavigableString):
                print('if_isinstance')
                print('current tag : ', type(current_tag),'----', current_tag)
                current_tag_str = current_tag.get_text().replace('\n','').encode('ISO-8859-1').decode('iso-8859-1')
                current_tag_str = ''.join(current_tag_str)
                contenu.append(current_tag_str)
            else:
                pass
            if index == 0:
                list_.append(('{}'.format(spk1), ''.join(contenu)+'**ALERT**'))
                print('contenu : ', contenu)
            elif index == 1:
                list_.append(('{}'.format(spk2), ''.join(contenu)+'**ALERT**'))
                print('contenu : ', contenu)
            else: 
                list_.append(('{}'.format(spk3), ''.join(contenu)+'**ALERT**'))
                print('contenu : ', contenu)
            try : 
                current_tag = current_tag.next_sibling
            except: 
                break # break out of the while loop if there are no more siblings
    return list_


In [46]:
def get_sync_multiple_loc2(turn, list_speaker):
    who_tags = turn.find_all('Who')
    liste_text = []
    for i, who_tag in enumerate(who_tags): 
        contenu = []
        current_tag = who_tag.next_sibling
        while current_tag is not None and current_tag.name != 'Who': 
            if isinstance(current_tag, NavigableString): 
                current_tag_str = current_tag.get_text()
                contenu.append(current_tag_str)
            else : 
                pass
            current_tag = current_tag.next_sibling
        liste_text.append(''.join(contenu).replace('\n',' ')+'**ALERT**')
    tour = list(zip(list_speaker, liste_text))
    return tour

In [47]:
liste = [parse_trs2(x, y) for x,y in zip(df_corpus['path_trs'].tolist(), df_corpus['corpus'].tolist())]

E:\Corpus\CLAPI_scrape\Clapi_Transcription_aperitif_entre_ami(e)s_glasgow.trs
No spk action :  ***ACTIONS***
---
MULTI SPEAKER
<Turn endTime="51.349" speaker="spk1 spk2" startTime="49.999">
<Sync time="49.999"/>
<Who nb="1"/>coucou<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Who nb="2"/>salut<Event desc=":" extent="previous" type="pronounce"/>
</Turn>
spk: spk1 text:  coucou  **ALERT**
<class 'str'>
_________________
spk: spk2 text:  salut **ALERT**
<class 'str'>
_________________
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="52.923" speaker="spk1" startTime="52.16">
<Sync time="52.16"/>ça va poulette<Event desc="/" extent="previous" type="pronounce"/>
</Turn>
ça va poulette

spk:  spk1 text :  ça va poulette
___________________
UN SEUL SPEAKER
<Turn endTime="53.432" speaker="spk2" startTime="52.923">
<Sync time="52.923"/>ouais<Event desc=":" extent="previous" type="pronounce"/> et toi<Event desc="/" exte

spk: spk1 text:  ouais c'est c'est pas un truc qui me**ALERT**
<class 'str'>
_________________
spk: spk2 text:  comme si tu me parlais de  mec qui travaille à la banque j'en sais rien tu vois**ALERT**
<class 'str'>
_________________
UN SEUL SPEAKER
<Turn endTime="3880.025" speaker="spk1" startTime="3872.906">
<Sync time="3872.906"/>nan mais c'est clair que ça te<Event desc=":" extent="previous" type="pronounce"/> ouais bref<Event desc="\" extent="previous" type="pronounce"/>
<Event desc="(.)" extent="instantaneous" type="noise"/> donc il a les cheveux un noir un peu<Event desc=":" extent="previous" type="pronounce"/> longs et tout<Event desc="\" extent="previous" type="pronounce"/> il est charmant</Turn>
nan mais c'est clair que ça te
 ouais bref

 donc il a les cheveux un noir un peu
 longs et tout
 il est charmant
spk:  spk1 text :  nan mais c'est clair que ça te ouais bref donc il a les cheveux un noir un peu longs et tout il est charmant
___________________
UN SEUL SPEAKER
<Turn en

No spk action :  ***ACTIONS***
---
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="414.201" speaker="spk3" startTime="412.575">
<Sync time="412.575"/>
<Comment desc="ouvre la porte"/>
</Turn>


spk:  spk3 text :  
___________________
MULTI SPEAKER
<Turn endTime="415.320" speaker="spk3 spk2" startTime="414.201">
<Sync time="414.201"/>
<Who nb="1"/>coucou<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Who nb="2"/>hello</Turn>
spk: spk3 text:  coucou    **ALERT**
<class 'str'>
_________________
spk: spk2 text:  hello**ALERT**
<class 'str'>
_________________
MULTI SPEAKER
<Turn endTime="417.111" speaker="spk1 spk2 spk3" startTime="415.320">
<Sync time="415.320"/>
<Who nb="1"/>salut<Who nb="2"/>bonjour *NNAAMMEE*<Who nb="3"/>
<Event desc="((rires))" extent="instantaneous" type="noise"/>
</Turn>
spk: spk1 text: 

________________________________________
E:\Corpus\CLAPI_scrape\Clapi_Transcription_aperitif_entre_ami(e)s_rupture.trs
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="12.006" speaker="spk1" startTime="11.313">
<Sync time="11.313"/>
<Comment desc="très aigu"/> coucou<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Comment desc="très aigu"/>
</Turn>

 coucou



spk:  spk1 text :   coucou
___________________
UN SEUL SPEAKER
<Turn endTime="13.654" speaker="spk2" startTime="12.006">
<Sync time="12.006"/>bonjour <Comment desc="rires"/>
</Turn>
bonjour 

spk:  spk2 text :  bonjour 
___________________
MULTI SPEAKER
<Turn endTime="15.445" speaker="spk1 spk2" startTime="13.654">
<Sync time="13.654"/>
<Who nb="1"/>ça a été pour l'étage<Event desc="/" extent="previous" type="pronounce"/>
<Event desc="(.)" extent="instantaneous" type="noise"/> tu t'es pas plantée<Event desc="/" extent="previous" type="pronounce"/>
<Who nb=

No spk action :  ***ACTIONS***
---
No spk action :  ***ACTIONS***
---
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="8.479" speaker="spk1" startTime="7.679">
<Sync time="7.679"/>ah salut</Turn>
ah salut
spk:  spk1 text :  ah salut
___________________
UN SEUL SPEAKER
<Turn endTime="9.372" speaker="spk2" startTime="8.479">
<Sync time="8.479"/>salut</Turn>
salut
spk:  spk2 text :  salut
___________________
UN SEUL SPEAKER
<Turn endTime="10.560" speaker="spk1" startTime="9.372">
<Sync time="9.372"/>coucou<Event desc=":" extent="previous" type="pronounce"/> ça va<Event desc="/" extent="previous" type="pronounce"/>
</Turn>
coucou
 ça va

spk:  spk1 text :  coucou ça va
___________________
UN SEUL SPEAKER
<Turn endTime="11.681" speaker="spk2" startTime="10.560">
<Sync time="10.560"/>ça va et toi<Event desc="/" extent="previous" type="pronounce"/>
</Turn>
ça va et toi

spk:  spk2 text :  ça va et toi
___________________
UN SEUL SPEAKER
<Turn endTime="12.915" speaker="spk1" s

...

<Turn endTime="3258.943" speaker="GU2" startTime="3226.420">
<Sync time="3226.420"/>c'est aussi la raison pour laquelle i ne va pas se marier<Event desc="\" extent="previous" type="pronounce"/> vraisemblablement<Event desc="\" extent="previous" type="pronounce"/>
<Sync time="3229.471"/>
<Event desc=".h" extent="previous" type="noise"/> il a pourtant<Event desc="/" extent="previous" type="pronounce"/> eu un fils<Event desc="/" extent="previous" type="pronounce"/> naturel<Event desc="\" extent="previous" type="pronounce"/> illégitime<Event desc="\" extent="previous" type="pronounce"/> david<Event desc="/" extent="previous" type="pronounce"/> qu'il a eu bon<Event desc="\" extent="previous" type="pronounce"/> alors euh<Event desc=":" extent="previous" type="pronounce"/>
<Event desc=":" extent="previous" type="pronounce"/>
<Comment desc="gestes circulaires avec les mains"/> ce sont des amours ancillaires<Event desc="\" extent="previous" type="pronounce"/>
<Sync time="3236.390"/>avec une don

No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="43.055" speaker="spk1" startTime="2.121"><Sync time="2.121"/>allez<Event desc="/" extent="previous" type="pronounce"/><Sync time="2.388"/><Event desc="3.3" extent="instantaneous" type="noise"/><Sync time="5.696"/>toi <Event desc="." extent="instantaneous" type="noise"/> tu laisses tes affaires dehors<Event desc="/" extent="previous" type="pronounce"/>_<Event desc="0.8" extent="instantaneous" type="noise"/> d'accord<Event desc="\" extent="previous" type="pronounce"/><Sync time="8.98"/><Comment desc="bruits"/><Sync time="15.181"/>je ferme la pOrte (crum) <Sync time="18.066"/><Event desc="2.0" extent="instantaneous" type="noise"/><Sync time="20.097"/>alors<Event desc="\" extent="previous" type="pronounce"/>_<Event desc="0.4" extent="instantaneous" type="noise"/> je sais peu de choses<Event desc="/" extent="previous" type="pronounce"/>_<Event desc="0.3" extent="instantaneous" type="noise"/> sauf que<Event desc="\" extent="pr

UN SEUL SPEAKER
<Turn endTime="0.804" speaker="spk1" startTime="0"><Sync time="0"/>c'est mon<Event desc=":" extent="previous" type="lexical"/></Turn>
c'est mon
spk:  spk1 text :  c'est mon
___________________
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="2.731" speaker="spk2" startTime="2.388"><Sync time="2.388"/>merci<Event desc="/" extent="previous" type="pronounce"/></Turn>
merci
spk:  spk2 text :  merci
___________________
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="5.193" speaker="spk1" startTime="3.787"><Sync time="3.787"/>j` vous la donnerai<Event desc=":" extent="previous" type="lexical"/><Event desc="/" extent="previous" type="pronounce"/> euh <Event desc="." extent="instantaneous" type="noise"/> plus tard<Event desc="/" extent="previous" type="pronounce"/></Turn>
j` vous la donnerai
 euh 
 plus tard
spk:  spk1 text :  j` vous la donnerai euh  plus tard
___________________
UN SEUL SPEAKER
<Turn endTime="5.954" speaker="spk2" startTime=

MULTI SPEAKER
<Turn endTime="1.851" mode="spontaneous" speaker="spk1 spk4" startTime="0"><Sync time="0"/><Who nb="1"/>mais j` vais m` prÃ©[senter<Event desc="/" extent="previous" type="pronounce"/> oui oui bien sÃ»r<Event desc="\" extent="previous" type="pronounce"/>]<Who nb="2"/>___________________[un indicateur<Event desc="\" extent="previous" type="pronounce"/>___________]</Turn>
spk: spk1 text:  mais j` vais m` prÃ©[senter oui oui bien sÃ»r]**ALERT**
<class 'str'>
_________________
spk: spk4 text:  ___________________[un indicateur___________]**ALERT**
<class 'str'>
_________________
No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="3.859" mode="spontaneous" speaker="spk1" startTime="2.383"><Sync time="2.383"/>on attend<Event desc="/" extent="previous" type="pronounce"/> euh<Event desc=":" extent="previous" type="lexical"/><Sync time="3.349"/><Event desc="0.5" extent="instantaneous" type="noise"/></Turn>
on attend
 euh
spk:  spk1 text :  on attend euh
______________

No spk action :  ***ACTIONS***
---
UN SEUL SPEAKER
<Turn endTime="43.055" speaker="spk1" startTime="2.121"><Sync time="2.121"/>allez<Event desc="/" extent="previous" type="pronounce"/><Sync time="2.388"/><Event desc="3.3" extent="instantaneous" type="noise"/><Sync time="5.696"/>toi <Event desc="." extent="instantaneous" type="noise"/> tu laisses tes affaires dehors<Event desc="/" extent="previous" type="pronounce"/>_<Event desc="0.8" extent="instantaneous" type="noise"/> d'accord<Event desc="\" extent="previous" type="pronounce"/><Sync time="8.98"/><Comment desc="bruits"/><Sync time="15.181"/>je ferme la pOrte (crum) <Sync time="18.066"/><Event desc="2.0" extent="instantaneous" type="noise"/><Sync time="20.097"/>alors<Event desc="\" extent="previous" type="pronounce"/>_<Event desc="0.4" extent="instantaneous" type="noise"/> je sais peu de choses<Event desc="/" extent="previous" type="pronounce"/>_<Event desc="0.3" extent="instantaneous" type="noise"/> sauf que<Event desc="\" extent="pr

In [48]:
liste[2].head()

startTime endTime           speaker speaker_native  \
0         0  11.313  ***NO SPEAKER***            NaN   
1    11.313  12.006               JUS         native   
2    12.006  13.654               ALB         native   
3    13.654  15.445               JUS         native   
4    13.654  15.445               ALB         native   

                                                text  \
0                                                NaN   
1                                             coucou   
2                                           bonjour    
3  ça a été pour l'étage  tu t'es pas plantée **A...   
4                                    ça va **ALERT**   

                                    text_synchronisé         audio_filename  \
0                                                NaN  aperitif_rupture_anon   
1            ('11.313', ['', ' coucou', '', '', ''])  aperitif_rupture_anon   
2                       ('12.006', ['bonjour ', ''])  aperitif_rupture_anon   
3  ('13.654', "ça a été pour l'étage  tu t'es pas...  aperitif_rupture_anon   
4                      ('13.654', 'ça va **ALERT**')  aperitif_rupture_anon   

  encoding                          corpus  
0    utf-8  aperitif_entre_ami(e)s_rupture  
1    utf-8  aperitif_entre_ami(e)s_rupture  
2    utf-8  aperitif_entre_ami(e)s_rupture  
3    utf-8  aperitif_entre_ami(e)s_rupture  
4    utf-8  aperitif_entre_ami(e)s_rupture

In [36]:
def add_metadata(df, dict_meta):
    x = df['corpus'].tolist()[0]
    length = len(df['corpus'].tolist())
    if x.replace('-', '').replace(' ', '').replace('_', '').lower() in dict_meta:
        responsable = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['corpus']['responsable_corpus']]*length
        duree = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['enregistrement']['duree_enregistrement']]*length
        description_enregistrement = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['enregistrement']['description_enregistrement']]*length
        date_enregistrement = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['enregistrement']['date_collecte_enregistrement']]*length
        langue_enregistrement = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['enregistrement']['langue_enregistrement']]*length
        lieu_enregistrement = [dict_meta['{}'.format(x.replace('-', '').replace(' ', '').replace('_', '').lower())]['enregistrement']['lieu_enregistrement']]*length

    else:
        responsable = ['NaN']*length
        duree = ['NaN']*length
        description_enregistrement = ['NaN']*length
        date_enregistrement = ['NaN']*length
        langue_enregistrement = ['NaN']*length
        lieu_enregistrement = ['NaN']*length
    df['responsable']=responsable
    df['duree']=duree
    df['description']=description_enregistrement
    df['date_enregistrement']=date_enregistrement
    df['langue_enregistrement']= langue_enregistrement
    df['lieu_enregistrement']= lieu_enregistrement
    loc_cara = ['nom_complet_speaker','sexe_speaker','age_speaker','profession_speaker', 'langue_speaker']
    val_loc = ['nom','sexe','age','profession', 'langue']
    for cara, val in zip(loc_cara, val_loc): 
        df['{}'.format(cara)] = df['speaker'].apply(lambda speaker : get_data_loc(x.replace('-', '').replace(' ', '').replace('_', '').lower(), speaker, dict_meta, val) if x.replace('-', '').replace(' ', '').replace('_', '').lower() in dict_meta else 'NaN')
    
    index = int(df_corpus.index[df_corpus['corpus'] == '{}'.format(x)].to_list()[0])
    path_trs = [df_corpus.loc[index, 'path_trs']]*length
    path_wav = [df_corpus.loc[index, 'path_wav']]*length
    df['path_trs'] = path_trs
    df['path_wav']= path_wav
    return df

In [37]:
def get_data_loc(name, speaker, corpus_dict, data):
    locuteurs = corpus_dict[name]['enregistrement']['locuteurs']
    for locuteur in locuteurs.values():
        if locuteur['speaker'] == speaker:
            return locuteur['{}'.format(data)]
    return None, None

In [38]:
liste = [add_metadata(df, dict_meta) for df in liste]

In [39]:
liste[2].head()

startTime endTime           speaker speaker_native  \
0         0  11.313  ***NO SPEAKER***            NaN   
1    11.313  12.006               JUS         native   
2    12.006  13.654               ALB         native   
3    13.654  15.445               JUS         native   
4    13.654  15.445               ALB         native   

                                          text  \
0                                          NaN   
1                                       coucou   
2                                     bonjour    
3  ça a été pour l'étage  tu t'es pas plantée    
4                                       ça va    

                                    text_synchronisé         audio_filename  \
0                                                NaN  aperitif_rupture_anon   
1            ('11.313', ['', ' coucou', '', '', ''])  aperitif_rupture_anon   
2                       ('12.006', ['bonjour ', ''])  aperitif_rupture_anon   
3  ('13.654', "ça a été pour l'étage  tu t'es pas...  aperitif_rupture_anon   
4                               ('13.654', 'ça va ')  aperitif_rupture_anon   

  encoding                          corpus  \
0    utf-8  aperitif_entre_ami(e)s_rupture   
1    utf-8  aperitif_entre_ami(e)s_rupture   
2    utf-8  aperitif_entre_ami(e)s_rupture   
3    utf-8  aperitif_entre_ami(e)s_rupture   
4    utf-8  aperitif_entre_ami(e)s_rupture   

                                     responsable  ... date_enregistrement  \
0  G. Icor, J. DuchanoisConseil de gestion Clapi  ...          8 Nov 2009   
1  G. Icor, J. DuchanoisConseil de gestion Clapi  ...          8 Nov 2009   
2  G. Icor, J. DuchanoisConseil de gestion Clapi  ...          8 Nov 2009   
3  G. Icor, J. DuchanoisConseil de gestion Clapi  ...          8 Nov 2009   
4  G. Icor, J. DuchanoisConseil de gestion Clapi  ...          8 Nov 2009   

  langue_enregistrement       lieu_enregistrement nom_complet_speaker  \
0              français  FRANCE  Région Lyonnaise        (None, None)   
1              français  FRANCE  Région Lyonnaise             Justine   
2              français  FRANCE  Région Lyonnaise              Albine   
3              français  FRANCE  Région Lyonnaise             Justine   
4              français  FRANCE  Région Lyonnaise              Albine   

   sexe_speaker   age_speaker profession_speaker langue_speaker  \
0  (None, None)  (None, None)       (None, None)   (None, None)   
1         Femme       20 - 30       en scolarité       français   
2         Femme       20 - 30                          français   
3         Femme       20 - 30       en scolarité       français   
4         Femme       20 - 30                          français   

                                            path_trs  \
0  E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
1  E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
2  E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
3  E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   
4  E:\Corpus\CLAPI_scrape\Clapi_Transcription_ape...   

                                            path_wav  
0  E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...  
1  E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...  
2  E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...  
3  E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...  
4  E:\Corpus\CLAPI_scrape\Clapi_Signal_aperitif_e...  

[5 rows x 22 columns]

In [40]:
df_tours = pd.concat(liste)

In [41]:
df_tours.rename(columns={'corpus': 'sous_corpus'}, inplace=True)

In [42]:
df_tours['corpus'] = ['CLAPI']*len(df_tours)

In [43]:
df_tours

startTime   endTime           speaker speaker_native  \
0           0    49.999  ***NO SPEAKER***            NaN   
1      49.999    51.349               JUD         native   
2      49.999    51.349               PAT         native   
3      51.349     52.16  ***NO SPEAKER***            NaN   
4       52.16    52.923               JUD         native   
..        ...       ...               ...            ...   
766  2150.418  2151.294               AME         native   
767  2151.294  2159.351               CPE         native   
768  2159.351  2159.838               KAR         native   
769  2159.838  2162.078               CPE         native   
770  2162.078  2175.661  ***NO SPEAKER***            NaN   

                                      text_synchronisé  \
0                                                  NaN   
1                               ('49.999', 'coucou  ')   
2                                 ('49.999', 'salut ')   
3                                                  NaN   
4                    ('52.16', ['ça va poulette', ''])   
..                                                 ...   
766                           ('2150.418', ['Hm hm '])   
767  ('2151.294', ['bon']), ('2151.806', []), ('215...   
768                          ('2159.351', ['Â°hmÂ° '])   
769  ('2159.838', ["d'accord"]), ('2160.540', []), ...   
770                                                NaN   

                                                  text  \
0                                                  NaN   
1                                             coucou     
2                                               salut    
3                                                  NaN   
4                                       ça va poulette   
..                                                 ...   
766                                             Hm hm    
767  bonalors j` vous donne ce papier-lÃ  pour vous...   
768                                            Â°hmÂ°    
769                                      d'accordallez   
770                                                NaN   

                            audio_filename    encoding  \
0                    Aperitif_glasgow_anon       utf-8   
1                    Aperitif_glasgow_anon       utf-8   
2                    Aperitif_glasgow_anon       utf-8   
3                    Aperitif_glasgow_anon       utf-8   
4                    Aperitif_glasgow_anon       utf-8   
..                                     ...         ...   
766  Bureau-CPE-probleme-petit-copain_anon  ISO-8859-1   
767  Bureau-CPE-probleme-petit-copain_anon  ISO-8859-1   
768  Bureau-CPE-probleme-petit-copain_anon  ISO-8859-1   
769  Bureau-CPE-probleme-petit-copain_anon  ISO-8859-1   
770  Bureau-CPE-probleme-petit-copain_anon  ISO-8859-1   

                        sous_corpus                              responsable  \
0    aperitif_entre_ami(e)s_glasgow  G. Icor, J. GayConseil de gestion Clapi   
1    aperitif_entre_ami(e)s_glasgow  G. Icor, J. GayConseil de gestion Clapi   
2    aperitif_entre_ami(e)s_glasgow  G. Icor, J. GayConseil de gestion Clapi   
3    aperitif_entre_ami(e)s_glasgow  G. Icor, J. GayConseil de gestion Clapi   
4    aperitif_entre_ami(e)s_glasgow  G. Icor, J. GayConseil de gestion Clapi   
..                              ...                                      ...   
766              Bureau_CPE_bagarre          G. IcorConseil de gestion Clapi   
767              Bureau_CPE_bagarre          G. IcorConseil de gestion Clapi   
768              Bureau_CPE_bagarre          G. IcorConseil de gestion Clapi   
769              Bureau_CPE_bagarre          G. IcorConseil de gestion Clapi   
770              Bureau_CPE_bagarre          G. IcorConseil de gestion Clapi   

     ... langue_enregistrement           lieu_enregistrement  \
0    ...              français  FRANCE Lyon Région Lyonnaise   
1    ...              français  FRANCE Lyon Région Lyonnaise   
2    ...              français  FRANCE 

# def iso2utf8(df):
    #/!\les str en iso sont mal lus par le programme
    # améliorer la synchronisation du texte 

In [44]:
df_tours.to_csv('E:\Corpus\CLAPI_scrape\CLAPI_TOTAL.csv', sep='\t', encoding='utf-8', index=False)

# XML TEI

In [67]:
def find_xml_files(folder_path):
    trs_paths = []
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            if file.endswith('.xml') or re.match(r'\d+_XML\.xml$', file):
                trs_paths.append(os.path.join(root, file))
    return trs_paths

In [68]:
def get_all_tagsname(xml_file):
    try : 
        tree = ET.parse(xml_file)
    # Get the root element of the tree
        root = tree.getroot()
    # Initialize an empty set to store the tag names
        tag_names = set()
    # Iterate over all elements in the tree and add their tag names to the set
        for elem in root.iter():
            tag_names.add(elem.tag)
    # Return the set of tag names
    except: 
        return "Pas de fichier trouvé à cet emplacement"
    return tag_names

In [69]:
def detect_encoding(file):
    with open(file, 'rb') as f:
        result = chardet.detect(f.read())
        encoding = result['encoding'] 
    # Open the file with the detected encoding
    with open(file, 'r', encoding=encoding) as f:
        soup = BeautifulSoup(f, "lxml-xml")
    return soup

In [70]:
def parse_trs(path):
    soup = detect_encoding(path)
    tagsname = list(get_all_tagsname(path))
    df = pd.DataFrame({'tagsname': [tagsname], 'path_trs':path})
    return df

In [71]:
folder_path = 'E:\Corpus\CLAPI_scrape'
xml_paths = find_xml_files(folder_path)
liste_xml = [parse_trs(xml) for xml in xml_paths]
df_xml = pd.concat(liste_xml, axis=0)

In [72]:
xml_paths

['E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_7_p_7.11_i_68_2014_03_06.xml',
 'E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_6_alix_6.01_23_2014_03_06.xml',
 'E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_5_tamara_5.08_67_2014_03_06 (1).xml',
 'E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_6_ludovic_6.00_58_2014_03_06.xml',
 'E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_7_p_7.04_h_39_2014_03_06 (1).xml',
 'E:\\Corpus\\CLAPI_scrape\\TEI___histoire_grenouil_7_p_7.04_z_41_2014_03_06.xml']